In [6]:
import pandas as pd
import scipy.spatial.distance as sci_dist
import matplotlib
matplotlib.use('QtAgg')
import seaborn as sns
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
import matplotlib
Image.MAX_IMAGE_PIXELS = None
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import poisson
import os
np.random.seed(0)
matplotlib.rcParams['pdf.fonttype'] = 42

plt.rcParams['font.family'] = 'sans-serif'
plt.rcParams['font.sans-serif'] = ['Arial']

data_folder = '/Users/yaelheyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/roi_2/exports'
region_data = '/Users/YaelHeyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/Region_Data_with_Minimal_Values.csv'

cell_by_gene_path = data_folder + '/cell_by_gene_matrix_dilate10_20240718_withbarcodes_atleast3.csv'
transcripts_path = data_folder + '/decode_1_withcoordinates.csv'
coords_path = data_folder + '/segmentation_1_nuclei_cellattributes.csv'
output_folder = data_folder + '/processedData'
cell_by_gene = pd.read_csv(cell_by_gene_path)


In [7]:
pixel2um = 107.11 / 1000000  # Convert pixel to micrometers
combined_df = pd.DataFrame()
region_data = pd.read_csv(region_data)
for j in range(1, 4):  # Adjust range as needed
    # Dynamically construct the path
    data_folder = f"/Users/yaelheyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/roi_{j}/exports"
    cell_by_gene_path = os.path.join(data_folder, 'cell_by_gene_matrix_dilate10_20240718_withbarcodes_clustering_10bcs_0.4thresh.csv')
    print(data_folder)
    # Load the cell by gene data
    cell_by_gene = pd.read_csv(cell_by_gene_path, index_col=0)
    
    # Get reference X and Y from region_data as scalar values
    ref_x = region_data.loc[region_data['Region'] == f"Region {j}", "Min X (mm)"].iloc[0]
    ref_y = region_data.loc[region_data['Region'] == f"Region {j}", "Min Y (mm)"].iloc[0]
    
    # Correct the coordinates
    cell_by_gene['center_x'] = (cell_by_gene['center_x'] * pixel2um + ref_x)*1000
    cell_by_gene['center_y'] = (cell_by_gene['center_y'] * pixel2um + ref_y)*1000
    
    # Adjust the cell_id to make them unique across regions
    cell_by_gene['cell_id'] = cell_by_gene['cell_id'] + j * 100000
    
    # Concatenate to the combined DataFrame
    combined_df = pd.concat([combined_df, cell_by_gene], ignore_index=True)


/Users/yaelheyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/roi_1/exports
/Users/yaelheyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/roi_2/exports
/Users/yaelheyman/RajLab Dropbox/Yael Heyman/SpatialBarcodes/ImagingData/2024-05-21_mouseexp_expression/projects/roi_3/exports


In [8]:
barcode_indices = {}
cell_by_gene = combined_df
# Loop through each barcode and add its index to the appropriate list
for index, barcode in enumerate(cell_by_gene['barcode_names']):
    # Convert NaN values to a string representation to handle them as unique keys
    barcode_key = barcode if barcode == barcode else 'NaN'
    if barcode_key in barcode_indices:
        barcode_indices[barcode_key].append(index)
    else:
        barcode_indices[barcode_key] = [index]

# Convert the dictionary to a list of lists (containing the indices)
indices_list = list(barcode_indices.values())
for ids in indices_list:
    print('ids')
    print(ids)
    for id in ids:
        if(id>0):
            print(cell_by_gene.loc[id,"barcode_names"])
unique_index_list = [
    cell_by_gene.loc[ids[0], ["barcode_names", "n_called_barcodes"]]
    for ids in indices_list
    if pd.notna(cell_by_gene.loc[ids[0], "barcode_names"])
]
unique_index_df = pd.DataFrame(unique_index_list, columns=["barcode_names", "n_called_barcodes"])
# Now you can access the column:
unique_index_df["barcode_names"]
print('Percentage zero barcodes: ' + str(np.sum(pd.isna(cell_by_gene['barcode_names'])) / len(cell_by_gene)))


ids
[0, 2, 3, 4, 5, 6, 11, 13, 22, 24, 25, 29, 31, 33, 35, 37, 45, 53, 55, 57, 61, 63, 64, 65, 66, 67, 70, 74, 78, 79, 80, 81, 82, 83, 85, 86, 87, 88, 89, 90, 91, 92, 95, 96, 97, 99, 103, 105, 106, 107, 108, 109, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 130, 132, 134, 136, 137, 140, 142, 144, 148, 150, 151, 153, 158, 160, 162, 166, 168, 175, 179, 180, 181, 183, 185, 188, 189, 190, 191, 192, 193, 194, 196, 199, 204, 208, 211, 213, 214, 220, 223, 224, 225, 229, 230, 234, 236, 237, 239, 240, 245, 248, 251, 252, 255, 257, 265, 269, 270, 271, 272, 273, 274, 284, 287, 288, 291, 292, 294, 301, 303, 305, 307, 310, 319, 324, 325, 326, 327, 328, 330, 334, 336, 339, 341, 342, 344, 351, 352, 357, 358, 359, 363, 366, 368, 373, 375, 377, 380, 384, 387, 392, 393, 401, 402, 404, 410, 413, 417, 420, 423, 426, 434, 446, 452, 455, 456, 462, 463, 464, 465, 468, 473, 475, 476, 477, 482, 485, 487, 494, 498, 502, 508, 527, 530, 532, 534, 535, 543, 547, 548, 550, 55

In [9]:
# data =unique_index_df["n_called_barcodes"]  #if using the grouping logic
data = cell_by_gene["n_called_barcodes"] #if going for direct count
# Estimate the lambda (mean) of the Poisson distribution
lambda_estimate = np.mean(data)
lambda_estimate 
# Calculate the empirical PMF
unique_values, counts = np.unique(data, return_counts=True)
empirical_pmf = counts / len(data)

# Theoretical Poisson PMF
x_values = np.arange(0, max(data) + 1)  # Range of possible values
theoretical_pmf = poisson.pmf(x_values, mu=lambda_estimate)

# Plotting the PMF
plt.figure(figsize=(2,2))

# Empirical PMF as a bar plot
plt.bar(unique_values, empirical_pmf, width=0.4, label='Empirical PMF', alpha=0.7, align='center')

# Theoretical Poisson PMF as a line plot
# plt.plot(x_values, theoretical_pmf, 'go-', label=f'Theoretical Poisson PMF (λ={lambda_estimate:.1f})')
plt.xlim([-1,16])
# Labels and legend
plt.xlabel('Number of barcodes per cell')
plt.ylabel('Probability')
plt.title('Empirical vs theoretical PDF')
plt.legend(bbox_to_anchor=(1.05, 0.5),
          loc='center left',
          borderaxespad=0)
plt.grid(True)
plt.savefig(output_folder + '/empirical vs predicted pdf tumor unclusstered.pdf',bbox_inches='tight')
plt.show()


In [10]:
cdf = np.empty(0)
for i in range(len(unique_values)):
    cdf = np.append(cdf, np.sum(empirical_pmf[i:]))
cdf_df = pd.DataFrame({ 'num barcodes': unique_values,'cdf': cdf}) 
# cdf_df.to_csv(os.path.join(output_folder, 'cdf vs unique number of barcodes.csv'))